# import 3commas dependencies

In [1]:
#!/usr/bin/env python3
import os
import sys
import time
import json
import argparse
from pathlib import Path

# import FB and san dependencies

In [2]:
import pandas as pd
from prophet import Prophet
from datetime import date
import san
san.ApiConfig.api_key = 'l5xaofjydbsmnivh_t3ioip3icldqopkd'
from san.extras.event_study import event_study, signals_format, hypothesis_test
import pandas as pd
from sklearn.metrics import mean_squared_error

# Set variables for Prohet

In [3]:
symbol='flow'
TF='1h'
stime="2021-01-27"


if TF !='1d':
    format='%Y-%m-%d %H:%M:%S'   
else:
    format='%Y-%m-%d'

# Read Data and Process Dates

In [4]:
from datetime import datetime, timedelta
import ciso8601
data=pd.DataFrame()
get_df=pd.DataFrame()


start_date=ciso8601.parse_datetime(stime)
end_date=datetime.now()#- timedelta(days=120)
step= 100
numdays = (end_date- start_date).days 
start_dt=start_date
#for h in range(0,numdays,step
h=0
end_dt=start_dt
while end_dt<datetime.now():   
    start_dt= datetime.now()- timedelta(days=numdays-h)   
    if start_dt>datetime.now():
        break
    end_dt=start_dt+timedelta(days=step) 
    if end_dt>datetime.now():
        end_dt=datetime.now()-timedelta(days=1)
    print ('Get FLOW price data from: ', start_date, ' to: ', end_date)
    print('Reqest #:',h,' Date: ',end_dt,' get days:',(end_dt-start_dt).days)
    get_df= san.get("ohlcv/"+symbol, 
    from_date=start_dt,
    to_date=end_dt,
    interval=TF).closePriceUsd
    data=pd.concat([data,get_df] )
    h=h+step
data.columns=['Price']
df=data
df.index=pd.to_datetime(df.index).strftime(format)
df['ds'] = pd.to_datetime(df.index)
df_prohet=pd.DataFrame()
df_no_index = df.reset_index(drop=True)
df_prohet['y']=df_no_index['Price']
df_prohet['ds']=df_no_index['ds']



Get FLOW price data from:  2021-01-27 00:00:00  to:  2022-05-14 04:07:59.100042
Reqest #: 0  Date:  2021-05-07 04:07:59.100042  get days: 100
Get FLOW price data from:  2021-01-27 00:00:00  to:  2022-05-14 04:07:59.100042
Reqest #: 100  Date:  2021-08-15 04:08:02.002757  get days: 100
Get FLOW price data from:  2021-01-27 00:00:00  to:  2022-05-14 04:07:59.100042
Reqest #: 200  Date:  2021-11-23 04:08:04.834638  get days: 100
Get FLOW price data from:  2021-01-27 00:00:00  to:  2022-05-14 04:07:59.100042
Reqest #: 300  Date:  2022-03-03 04:08:07.723221  get days: 100
Get FLOW price data from:  2021-01-27 00:00:00  to:  2022-05-14 04:07:59.100042
Reqest #: 400  Date:  2022-05-13 04:08:10.272958  get days: 71


# Train Model

In [5]:
m = Prophet(interval_width=0.95, 
    daily_seasonality=True,
    weekly_seasonality=True,
    yearly_seasonality=True,
    changepoint_prior_scale=0.5,
    seasonality_mode='multiplicative',
    seasonality_prior_scale=0.01
    )
model = m.fit(df_prohet)

# Forecast Away

In [6]:
future = m.make_future_dataframe(periods=30,freq=TF)
forecast = m.predict(future)
forecast2 = forecast.set_index ('ds')
df_plt=df.set_index ('ds')
y=df_plt['2021-01-01': ]['Price']
df_plt=df.set_index ('ds')
y=df_plt['2021-01-01': ]['Price']
yhat=forecast2['2021-01-01': ]['yhat']
yhat_upper=forecast2['2021-01-01': ]['yhat_upper']
yhat_lowwer=forecast2['2021-01-01': ]['yhat_lower']
# import plotly packages 
import plotly.graph_objects as go
import plotly.express as px

x=forecast2['2021-01-01': ].index.strftime(format)
real_price=go.Scatter(x=x, 
        y=y['2021-01-01':], 
        name='Real '+symbol,
        line = dict(color = 'firebrick', width = 1),
        text = x,
        #mode = 'markers',
        marker=dict(color='#ffcdd2')
        #marker = dict(size = 1,color = 'firebrick',opacity = 0.5),
        #hoverinfo = 'text+y+name'
        )
prediction_price=go.Scatter(x=x, y=yhat['2021-01-01':], name='Predicted '+symbol,\
        line = dict(color = 'blue', width = 1),
        text = x,
        #mode = 'markers',
        #marker = dict(size = 1,color = 'blue',opacity = 0.5),
        hoverinfo = 'text+y+name')
upper=go.Scatter(x=x, y=yhat_upper['2021-01-01':], name='Upper Bound',\
        line = dict(color = 'green', width = 1),
        text = x,
        #mode = 'markers',
        #marker = dict(size = 1,color = 'green',opacity = 0.5),
        hoverinfo = 'text+y+name')
lower=go.Scatter(x=x, y=yhat_lowwer['2021-01-01':], name='Lower Bound',\
        line = dict(color = 'red', width = 1),
        text = x,
        #mode = 'markers',
        #marker = dict(size = 1,color = 'red',opacity = 0.5),
        hoverinfo = 'text+y+name')        
fig=go.Figure(data=[real_price,prediction_price,upper,lower])


#  Plotting   

In [7]:
# step 2 : Setting the update_layout function   
fig.update_layout(title='Predicted '+symbol,
                   xaxis_title='Date',
                   yaxis_title='Predicted '+symbol,
                   font=dict(family='Courier New, monospace'),
                   legend_orientation="v",                   
                   hovermode='closest'
                   )

# Get last data

In [8]:
# Python
def stan_init(m):
    """Retrieve parameters from a trained model.
    
    Retrieve parameters from a trained model in the format
    used to initialize a new Stan model.
    
    Parameters
    ----------
    m: A trained model of the Prophet class.
    
    Returns
    -------
    A Dictionary containing retrieved parameters of m.
    
    """
    res = {}
    for pname in ['k', 'm', 'sigma_obs']:
        res[pname] = m.params[pname][0][0]
    for pname in ['delta', 'beta']:
        res[pname] = m.params[pname][0]
    return res

# Create or load 3commas configuration file

In [9]:
import gridbot as Gb



INFO:root:3C Cyber Bot-Helper _gridbot.ini
2022-05-14 04:10:34 - _gridbot.ini - INFO - 3C Cyber Bot-Helper _gridbot.ini
INFO:root:Started on Saturday 04:10:34 2022-05-14
2022-05-14 04:10:34 - _gridbot.ini - INFO - Started on Saturday 04:10:34 2022-05-14
INFO:root:Notifications are disabled
2022-05-14 04:10:34 - _gridbot.ini - INFO - Notifications are disabled


# Initialize 3Commas API

In [10]:
# Initialize 3Commas API



# Auto tune a running gridbot
while True:
    #config = Gb.load_config(datadir,program)
    #Gb.logger.info(f"Reloaded configuration from '{datadir}/{program}.ini'")

    get_last_df= san.get("ohlcv/"+symbol, 
    from_date=datetime.now()-timedelta(days=1),
    to_date=datetime.now()+timedelta(days=1),
    interval=TF).closePriceUsd

    last_data=pd.DataFrame(get_last_df)
    last_data.columns=['Price']
    conv_last_data=last_data
    conv_last_data.index = pd.to_datetime(last_data.index)

    conv_last_data.index=pd.to_datetime(conv_last_data.index).strftime(format)
    conv_last_data['ds'] = pd.to_datetime(conv_last_data.index)
    last_df_prohet=pd.DataFrame()
    last_df_no_index = conv_last_data.reset_index(drop=True)
    last_df_prohet['y']=last_df_no_index['Price']
    last_df_prohet['ds']=last_df_no_index['ds']
    
    m2 = Prophet(interval_width=0.95, 
        daily_seasonality=True,
        weekly_seasonality=True,
        yearly_seasonality=True,
        changepoint_prior_scale=0.5,
        seasonality_mode='multiplicative',
        seasonality_prior_scale=0.01
        ).fit(df_prohet, init=stan_init(m))  # Adding the last day, warm-starting from m1

    future2 = m2.make_future_dataframe(periods=24*3,freq=TF)
    forecast3 = m2.predict(future2)

    last_price=round(san.get("ohlcv/"+symbol, 
        from_date=datetime.now()-timedelta(days=1),
        to_date=datetime.now(),
        interval='1m').tail(1).closePriceUsd.mean(),3)
    #last_price=round(forecast3.loc[forecast3['ds']<datetime.now(),'yhat'].tail(1).mean(),3)

    trend=forecast3.loc[forecast3['ds']>datetime.now()+timedelta(hours=24),'trend'].tail(3).mean()-\
        forecast3.loc[forecast3['ds']<datetime.now()-timedelta(hours=24),'trend'].tail(3).mean()
    
    up_lvl=round(forecast3.loc[forecast3['ds']>datetime.now()+timedelta(hours=24),'yhat_upper'].head(1).mean(),3)
    low_lvl=round(forecast3.loc[forecast3['ds']>datetime.now()+timedelta(hours=24),'yhat_lower'].head(1).mean(),3)
    
    if trend<0:    
        upper_price=up_lvl
        lower_price=last_price
    else:    
        lower_price=low_lvl
        upper_price=last_price
    
    if last_price>up_lvl:
        upper_price=up_lvl*1.1
        lower_price=last_price

    if last_price<low_lvl:
        lower_price=low_lvl*0.9
        upper_price=last_price
    #upper_price=10
    # Configuration settings
    timeint = int(Gb.config.get("settings", "timeinterval"))
    botids = json.loads(Gb.config.get("settings", "botids"))

    # Walk through all bots specified
    for bot in botids:
        boterror, botdata = Gb.api.request(
            entity="grid_bots",
            action="get",
            action_id=str(bot),
        )
        if botdata:
            #Gb.logger.debug("Raw Gridbot data: %s" % botdata)
            print('New Upper Price: ',upper_price)
            print('New Lower Price: ',lower_price)   
            Gb.manage_gridbot(botdata, upper_price, lower_price)
        else:
            Gb.logger.error("Error occurred managing gridbots: %s" % boterror["msg"])
    if not Gb.wait_time_interval(Gb.logger, Gb.notification, timeint):
        break  
    

INFO:root:Current settings for 'My Grid Bot #1321531':
2022-05-14 04:10:54 - _gridbot.ini - INFO - Current settings for 'My Grid Bot #1321531':
INFO:root:Pair: USDT_FLOWUSDT
2022-05-14 04:10:54 - _gridbot.ini - INFO - Pair: USDT_FLOWUSDT
INFO:root:Upper price: 6.746
2022-05-14 04:10:54 - _gridbot.ini - INFO - Upper price: 6.746
INFO:root:Lower price: 2.986
2022-05-14 04:10:54 - _gridbot.ini - INFO - Lower price: 2.986
INFO:root:Quantity per grid: 300.0
2022-05-14 04:10:54 - _gridbot.ini - INFO - Quantity per grid: 300.0
INFO:root:Grid quantity: 100
2022-05-14 04:10:54 - _gridbot.ini - INFO - Grid quantity: 100
INFO:root:Strategy type: manual
2022-05-14 04:10:54 - _gridbot.ini - INFO - Strategy type: manual
INFO:root:Current price for USDT_FLOWUSDT is 2.959
2022-05-14 04:10:54 - _gridbot.ini - INFO - Current price for USDT_FLOWUSDT is 2.959
INFO:root:Grid of gridbot 'My Grid Bot #1321531' with pair USDT_FLOWUSDT will be adjusted like this:
Upper: 6.746 -> 6.449 Lower: 2.986 -> 2.986
202

New Upper Price:  6.449
New Lower Price:  2.986


INFO:root:Moved the grid of gridbot 'My Grid Bot #1321531' using pair USDT_FLOWUSDT with upper and lower price: 6.449 - 2.986
2022-05-14 04:10:56 - _gridbot.ini - INFO - Moved the grid of gridbot 'My Grid Bot #1321531' using pair USDT_FLOWUSDT with upper and lower price: 6.449 - 2.986
INFO:root:Activated gridbot '1321531'
2022-05-14 04:10:57 - _gridbot.ini - INFO - Activated gridbot '1321531'
INFO:root:Next update in 3600 Seconds at 05:10:57
2022-05-14 04:10:57 - _gridbot.ini - INFO - Next update in 3600 Seconds at 05:10:57
